In [ ]:
# NECESSARY CELL TO REMOVE THE DOWNLOAD AND EXECUTE BUTTONS FROM THE PAGE 

# GPs for Regression

In order to use Gaussian Processes for regression, the first step is of course to observe some targets $\mbf{t}$. We again assume an observation model of the form:

$$
p(t\vert y) = \mathcal{N}\left(t\vert y(\mathbf{x}),\beta^{-1}\right)
$$(gprobservation)

which means that we observe $y$ only indirectly, polluted by a Gaussian noise with variance $\beta^{-1}$. With the usual *i.i.d.* assumption, we get that **conditioned on $y$**, individual target observations are independent from each other (*conditional independence*). 

Furthermore, we would also like to predict a new target value $\hat{t}$. With all this new information, we can adapt our graph model from before:

```{figure} ../../../images/gpgraph4.svg
:scale: 50%
:name: gpgraph4

A GP graph but now with noisy target observations and prediction for $y$ at a new input $\hat{\bx}$.
```

and following the joint distribution encoded by the graph (check this by hand!), we can arrive at a marginal for all our $N$ targets $\mbf{t}$ at (stacked) inputs $\mbf{X}$:

$$
p(\mbf{t}) = \displaystyle\int p(\mbf{t}\vert\mbf{y})p(\mbf{y})\,\mrm{d}\mbf{y} = \gauss\left(\mbf{t}\vert\mbf{0},K(\mbf{X},\mbf{X}) + \beta^{-1}\mbf{I}\right)
$$(gprmarginalt)

where we once again have simply followed the {ref}`standard result<bayes-stdexpressions>` for a Gaussian marginal under Bayesian inversion, in this case with $\bs{\Sigma} = K(\mbf{X},\mbf{X})$, $\mbf{A}=\mbf{I}$ and $\mbf{L}^{-1}=\beta^{-1}\mbf{I}$.

From Eq. {eq}`gpjointab` we have seen previously, we can now easily include $\hat{t}$ in the joint:

$$
p(\mbf{t},\cB{\hat{t}}) = 
\gauss\left(
\mbf{t},\cB{\hat{t}}\left\vert\right.\mbf{0},
\begin{bmatrix}
K\left(\mbf{X},\mbf{X}\right) + \beta^{-1}\mbf{I} &
\cE{K\left(\mbf{X},\hat{\bx}\right)} \\
\cA{K\left(\hat{\bx},\mbf{X}\right)} &
\cB{k\left(\hat{\bx},\hat{\bx}\right)} + \beta^{-1}
\end{bmatrix}
\right)
$$(gprjoint)

where you should pay special attention to what comes from $p(\mbf{y})$ and what comes from the observation model, namely the noise $\beta$. Finally, again using the {ref}`standard result<bayes-stdexpressions>` for multivariate Gaussians, we can condition $\hat{t}$ on $\mbf{t}$ and reach our **posterior predictive distribution**:

$$
p(\hat{t}\vert\mbf{t}) = \gauss\left(
\hat{t}\vert \hat{m},\hat{\sigma}^2
\right)
$$(gprposterior)

with posterior mean:

$$
\hat{m} = \cA{K\left(\hat{\bx},\mbf{X}\right)}
\left[
K\left(\mbf{X},\mbf{X}\right) + \beta^{-1}\mbf{I}
\right]^{-1}
\mbf{t}
$$(gprposteriormean)

and posterior variance:

$$
\hat{\sigma}^2 = \cB{k\left(\hat{\bx},\hat{\bx}\right)} - \cA{K\left(\hat{\bx},\mbf{X}\right)}
\left[
K\left(\mbf{X},\mbf{X}\right) + \beta^{-1}\mbf{I}
\right]^{-1}
\cE{K\left(\mbf{X},\hat{\bx}\right)} + \beta^{-1}
$$(gprposteriorvar)

and we can just as easily predict for multiple values of $\hat{t}$ at once by using a block $\hat{\bx}$, in which case the mean becomes a vector and the variance becomes a covariance matrix.

Look again at the expressions above: note how a GP for regression is a **non-parametric model**. Instead of storing information obtained during training in a weight vector, we always need the values of $\mbf{t}$ and $\mbf{X}$ to make new predictions.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from myst_nb import glue
from matplotlib.lines import Line2D
import torch
from cycler import cycler
import seaborn as sns

# Set the color scheme
sns.set_theme()
colors = ['#0076C2', '#EC6842', '#A50034', '#009B77', '#FFB81C', '#E03C31', '#6CC24A', '#EF60A3', '#0C2340', '#00B8C8', '#6F1D77']
plt.rcParams['axes.prop_cycle'] = cycler(color=colors)

c_mean = c_std = 'C0'

torch.set_default_tensor_type(torch.DoubleTensor)

def f (X):
    return np.sin(X)

def kernel (X1,X2,sigf,length):
    n1 = len(X1)
    n2 = len(X2)
        
    K = torch.zeros((n1,n2))
    
    for i in range(n1):
        for j in range(n2):
            K[i,j] = sigf**2 * torch.exp(-0.5 / length / length * (X1[i]-X2[j])**2.0)
    
    return K

def gp(X,y,logsig,loglen,lognoise,Xhat=None):
    sigf   = torch.exp(logsig)
    length = torch.exp(loglen)
    noise  = torch.exp(lognoise)
        
    K = kernel(X,X,sigf,length) + 1./noise * torch.eye(len(X))# + 1.e-0 * torch.eye(len(X))

    L = torch.linalg.cholesky(K)
    alpha = torch.cholesky_solve(torch.reshape(y,(-1,1)),L)
        
    if Xhat is not None:
        mean = kernel(Xhat,X,sigf,length) @ alpha
        
        cov  = kernel(Xhat,Xhat,sigf,length) - kernel(Xhat,X,sigf,length) @ torch.cholesky_solve(kernel(X,Xhat,sigf,length),L) + 1./noise * torch.eye(len(Xhat))

        return mean, cov - 1./noise * torch.eye(len(Xhat)), mean[:,0] - 1.96*torch.sqrt(torch.diagonal(cov)), mean[:,0] + 1.96*torch.sqrt(torch.diagonal(cov))
    else:       
        lml = -0.5 * torch.inner(y,alpha[:,0]) - torch.sum(torch.log(torch.diagonal(L))) - float(len(y)) / 2. * torch.log(torch.tensor(2.*torch.pi))
        
        return lml
   
torch.manual_seed(10)
np.random.seed(10)

N = 5

beta_true = 100.0

X = np.random.uniform(0,2*np.pi,N)
y = f(X) + np.random.normal(0.,np.sqrt(1./beta_true),N)

X = torch.tensor(X)
y = torch.tensor(y)

lsig = torch.tensor([np.log(1.)],requires_grad=True)
llen = torch.tensor([np.log(1.)],requires_grad=True)
lnoi = torch.tensor([np.log(1.)],requires_grad=True)

bfgs = torch.optim.LBFGS((lsig,llen,lnoi),max_iter=50)

losses = []
sigs   = []
lens   = []
noises = []

# for epoch in range(n_epochs):
def closure():
    bfgs.zero_grad()
    loss = -gp(X,y,lsig,llen,lnoi)
    loss.backward()
    # print('Grads:',lsig.grad[0],llen.grad[0],lnoi.grad[0])
    
    losses.append(loss.detach().numpy())
    sigs.append(np.exp(lsig.detach().numpy()[0]))
    lens.append(np.exp(llen.detach().numpy()[0]))
    noises.append(np.exp(lnoi.detach().numpy()[0]))

    return loss

bfgs.step(closure)

Xhat = np.linspace(0,2.*np.pi,100)

print('Final loss',losses[-1],'Sigf',sigs[-1],'Length scale',lens[-1],'Noise',noises[-1])

n_samples = 10

prior_mean = torch.zeros(len(Xhat))
prior_cov = kernel(Xhat,Xhat,torch.exp(lsig),torch.exp(llen))

prior_stdm = prior_mean - 1.96*torch.sqrt(torch.diagonal(prior_cov) + 1./torch.exp(lnoi))
prior_stdp = prior_mean + 1.96*torch.sqrt(torch.diagonal(prior_cov) + 1./torch.exp(lnoi))

prior_samples = np.random.multivariate_normal(prior_mean.detach().numpy(),prior_cov.detach().numpy(),n_samples)

post_mean, post_cov, post_stdm, post_stdp = gp(X,y,lsig,llen,lnoi,Xhat)

post_samples = np.random.multivariate_normal(post_mean[:,0].detach().numpy(),post_cov.detach().numpy(),n_samples)

fig0, (ax0,ax1) = plt.subplots(1,2,figsize=(10,3),dpi=400)
ax0.set_xlabel('x')
ax0.set_ylabel('y')
ax1.set_xlabel('x')
ax1.set_ylabel('t')
ax0.set_title('Prior')
ax1.set_title('Posterior')

for s in prior_samples:
    ax0.plot(Xhat,s,linewidth=1,alpha=0.5)

ax0.plot(Xhat,f(Xhat),'k--',label='Ground truth',linewidth=1)

ax0.fill_between(Xhat,prior_stdm.detach().numpy(),prior_stdp.detach().numpy(),
                 alpha=0.15,label='95% conf. interval', color=c_std)
ax0.plot(Xhat,prior_mean.detach().numpy(),label='Mean',color=c_mean,linewidth=2.5)

handles, labels = ax0.get_legend_handles_labels()
line = Line2D([0], [0], color='gray', lw=1,alpha=0.5)
handles.append(line)
labels.append('y(x) samples')
ax0.legend(handles=handles, labels=labels, fontsize=7)

for s in post_samples:
    ax1.plot(Xhat,s,linewidth=1,alpha=0.5)

ax1.plot(Xhat,f(Xhat),'k--',label='Ground truth',linewidth=1)

ax1.fill_between(Xhat,post_stdm.detach().numpy(),post_stdp.detach().numpy(),
                 alpha=0.15,label='95% conf. interval',color=c_std)
ax1.plot(Xhat,post_mean.detach().numpy(),label='Mean',color=c_mean,linewidth=2.5)

ax1.plot(X,y,'k.',markersize=8,label='Observations')


handles, labels = ax1.get_legend_handles_labels()
line = Line2D([0], [0], color='gray', lw=1,alpha=0.5)
handles.append(line)
labels.append('y(x) samples')
ax1.legend(handles=handles, labels=labels, fontsize=7)

glue("fig0",fig0,display=False)

Below you can see an example of GP model for regression for a one-dimensional input. We opt for a Squared Exponential kernel. On the left you can see the prior over $t$ (mean and two standard deviations) with draws from $y(x)$ also shown. On the right you can see the posterior over $\hat{t}$ for the whole domain including some draws from the posterior over functions $p(\mbf{y}\vert\mbf{t})$.

```{glue:figure} fig0
:figwidth: 750px

Example of GP for regression, prior (left) and posterior (right) over $t$, with ten function draws from $y(x)$ in each plot.
```

Note how all desirable features for a robust model are present:
- The model avoids overfitting even for very small datasets;
- Mean and sampled functions fit closely to the observed data;
- The variance gives a measure of prediction uncertainty, increasing away from the observations;
- Hyperparameters are learned directly from data without the need for a validation dataset.

In the next page we will go through this last point, namely how to determine suitable values for the kernel hyperparameters.